# Table of Contents
 <p><div class="lev1 toc-item"><a href="#Ground-predictions" data-toc-modified-id="Ground-predictions-1"><span class="toc-item-num">1&nbsp;&nbsp;</span>Ground predictions</a></div><div class="lev2 toc-item"><a href="#PVLib-Clearsky" data-toc-modified-id="PVLib-Clearsky-11"><span class="toc-item-num">1.1&nbsp;&nbsp;</span>PVLib Clearsky</a></div><div class="lev1 toc-item"><a href="#Train/test-on-NSRDB-data" data-toc-modified-id="Train/test-on-NSRDB-data-2"><span class="toc-item-num">2&nbsp;&nbsp;</span>Train/test on NSRDB data</a></div>

In [70]:
import pandas as pd
import numpy as np
import os
import datetime
import matplotlib
import matplotlib.pyplot as plt
from mpl_toolkits.axes_grid1 import make_axes_locatable
from sklearn import tree

import pytz
import itertools
import visualize
import utils
import pydotplus
import xgboost as xgb

from sklearn import metrics

import pvlib
import cs_detection_refactor as cs_detection
# import cs_detection_refactor
# import visualize
# from bokeh.plotting import output_notebook
# output_notebook()

import visualize_plotly as visualize

from IPython.display import Image

%load_ext autoreload
%autoreload 2

np.set_printoptions(precision=4)
%matplotlib notebook

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


# Ground predictions

## PVLib Clearsky

Only making ground predictions using PVLib clearsky model and statistical model.  NSRDB model won't be available to ground measurements.

In [71]:
nsrdb = cs_detection.ClearskyDetection.read_pickle('srrl_nsrdb_1.pkl.gz')
nsrdb.df.index = nsrdb.df.index.tz_convert('MST')

In [72]:
nsrdb.time_from_solar_noon('Clearsky GHI pvlib', 'tfn')

In [73]:
ground = cs_detection.ClearskyDetection.read_pickle('abq_ground_1.pkl.gz')
ground.df.index = ground.df.index.tz_convert('MST')

In [74]:
feature_cols = [
'tfn',
'abs_ideal_ratio_diff',
'abs_ideal_ratio_diff mean',
'abs_ideal_ratio_diff std',
# 'abs_ideal_ratio_diff max',
# 'abs_ideal_ratio_diff min',
# 'abs_ideal_ratio_diff range',
# 'abs_ideal_ratio_diff gradient',
# 'abs_ideal_ratio_diff gradient mean',
# 'abs_ideal_ratio_diff gradient std',
# 'abs_ideal_ratio_diff gradient max',
# 'abs_ideal_ratio_diff gradient min',
# 'abs_ideal_ratio_diff gradient range',
# 'abs_ideal_ratio_diff gradient second',
# 'abs_ideal_ratio_diff gradient second mean',
# 'abs_ideal_ratio_diff gradient second std',
# 'abs_ideal_ratio_diff gradient second max',
# 'abs_ideal_ratio_diff gradient second min',
# 'abs_ideal_ratio_diff gradient second range',
'GHI Clearsky GHI pvlib gradient ratio', 
'GHI Clearsky GHI pvlib gradient ratio mean', 
'GHI Clearsky GHI pvlib gradient ratio std', 
# 'GHI Clearsky GHI pvlib gradient ratio min', 
# 'GHI Clearsky GHI pvlib gradient ratio max', 
# 'GHI Clearsky GHI pvlib gradient ratio range', 
'GHI Clearsky GHI pvlib gradient second ratio', 
'GHI Clearsky GHI pvlib gradient second ratio mean', 
'GHI Clearsky GHI pvlib gradient second ratio std', 
# 'GHI Clearsky GHI pvlib gradient second ratio min', 
# 'GHI Clearsky GHI pvlib gradient second ratio max', 
# 'GHI Clearsky GHI pvlib gradient second ratio range',
'GHI Clearsky GHI pvlib line length ratio',
'GHI Clearsky GHI pvlib line length ratio gradient',
'GHI Clearsky GHI pvlib line length ratio gradient second'
]

target_cols = ['sky_status']

# Train/test on NSRDB data

In [75]:
train = cs_detection.ClearskyDetection(nsrdb.df)
train.trim_dates('01-01-2010', '01-01-2015')
test = cs_detection.ClearskyDetection(nsrdb.df)
test.trim_dates('01-01-2015', None)

In [76]:
import xgboost as xgb
# clf = xgb.XGBClassifier(max_depth=4, n_estimators=300, learning_rate=.01, nthread=4, min_child_weight=1)
clf = xgb.XGBClassifier(max_depth=3, n_estimators=400, learning_rate=.01, nthread=4, reg_lambda=1)
clf = xgb.XGBClassifier(**{'max_depth': 4, 'n_estimators': 500, 'learning_rate': 0.005, 'reg_lambda': 1}, n_jobs=4)

In [77]:
train.scale_model('GHI', 'Clearsky GHI pvlib', 'sky_status')

In [78]:
train.calc_all_window_metrics(train.df, 3, col1='GHI', col2='Clearsky GHI pvlib', overwrite=True)

In [79]:
clf.fit(train.df[feature_cols].values, train.df[target_cols].values.flatten())

XGBClassifier(base_score=0.5, booster='gbtree', colsample_bylevel=1,
       colsample_bytree=1, gamma=0, learning_rate=0.005, max_delta_step=0,
       max_depth=4, min_child_weight=1, missing=None, n_estimators=500,
       n_jobs=4, nthread=None, objective='binary:logistic', random_state=0,
       reg_alpha=0, reg_lambda=1, scale_pos_weight=1, seed=None,
       silent=True, subsample=1)

In [80]:
# pred = clf.predict(test.df[feature_cols].values)
pred = test.iter_predict_daily(feature_cols, 'GHI', 'Clearsky GHI pvlib', clf, 3)
pred = pred.astype(bool)

In [81]:
vis = visualize.Visualizer()
vis.add_line_ser(test.df['GHI'], 'GHI')
vis.add_line_ser(test.df['Clearsky GHI pvlib'], 'GHI_cs')
vis.add_circle_ser(test.df[(test.df['sky_status'] == 0) & (pred)]['GHI'], 'ML clear only')
vis.add_circle_ser(test.df[(test.df['sky_status'] == 1) & (~pred)]['GHI'], 'NSRDB clear only')
vis.add_circle_ser(test.df[(test.df['sky_status'] == 1) & (pred)]['GHI'], 'ML+NSRDB clear only')
vis.add_line_ser(test.df['abs_ideal_ratio_diff'] * 100, 'ZZZ')
vis.show()

model and measure appear to be mismatched in the early mornings and late eveings (during summer months especially).

In [82]:
cm = metrics.confusion_matrix(test.df['sky_status'].values, pred)
vis = visualize.Visualizer()
vis.plot_confusion_matrix(cm, labels=['cloudy', 'clear'])

In [83]:
train = cs_detection.ClearskyDetection(nsrdb.df)
# train.trim_dates('01-01-2010', None)
train.scale_model('GHI', 'Clearsky GHI pvlib', 'sky_status')
train.calc_all_window_metrics(train.df, 3, col1='GHI', col2='Clearsky GHI pvlib', overwrite=True)
clf.fit(train.df[feature_cols].values, train.df[target_cols].values.flatten())

XGBClassifier(base_score=0.5, booster='gbtree', colsample_bylevel=1,
       colsample_bytree=1, gamma=0, learning_rate=0.005, max_delta_step=0,
       max_depth=4, min_child_weight=1, missing=None, n_estimators=500,
       n_jobs=4, nthread=None, objective='binary:logistic', random_state=0,
       reg_alpha=0, reg_lambda=1, scale_pos_weight=1, seed=None,
       silent=True, subsample=1)

In [84]:
test = cs_detection.ClearskyDetection(ground.df)

In [85]:
test.intersection(train.df.index)

In [86]:
test.trim_dates('10-08-2010', '10-16-2010')

In [87]:
test.time_from_solar_noon('Clearsky GHI pvlib', 'tfn')

In [88]:
# pred = clf.predict(test.df[feature_cols].values)
pred = test.iter_predict_daily(feature_cols, 'GHI', 'Clearsky GHI pvlib', clf, 3)
pred = pred.astype(bool)

AttributeError: 'RangeIndex' object has no attribute 'date'

In [ ]:
train.intersection(test.df.index)

In [ ]:
vis = visualize.Visualizer()

In [ ]:
vis.add_line_ser(test.df['GHI'], 'GHI')
vis.add_line_ser(test.df['Clearsky GHI pvlib'], 'GHI_cs')
vis.add_circle_ser(test.df[(train.df['sky_status'] == 0) & (pred)]['GHI'], 'ML clear only')
vis.add_circle_ser(test.df[(train.df['sky_status'] == 1) & (~pred)]['GHI'], 'NSRDB clear only')
vis.add_circle_ser(test.df[(train.df['sky_status'] == 1) & (pred)]['GHI'], 'ML+NSRDB clear only')

In [ ]:
vis.show()

In [ ]:
ground = cs_detection.ClearskyDetection.read_pickle('srrl_ground_1.pkl.gz')

In [ ]:
ground.df.index = ground.df.index.tz_convert('MST')

In [ ]:
ground.trim_dates('10-01-2010', '10-15-2010')

In [ ]:
ground.time_from_solar_noon('Clearsky GHI pvlib', 'tfn')

In [ ]:
test = ground

In [ ]:
%%time
import warnings
warnings.simplefilter("ignore")
pred = test.iter_predict_daily(feature_cols, 'GHI', 'Clearsky GHI pvlib', clf, 60)
pred = pred.astype(bool)

In [ ]:
vis = visualize.Visualizer()

In [ ]:
vis.add_line_ser(test.df['GHI'], 'GHI')
vis.add_line_ser(test.df['Clearsky GHI pvlib'], 'GHI_cs')
vis.add_circle_ser(test.df[(test.df['sky_status pvlib'] == 0) & (pred)]['GHI'], 'ML clear only')
vis.add_circle_ser(test.df[(test.df['sky_status pvlib'] == 1) & (~pred)]['GHI'], 'PVLib clear only')
vis.add_circle_ser(test.df[(test.df['sky_status pvlib'] == 1) & (pred)]['GHI'], 'ML+PVLib clear only')

In [ ]:
vis.show()

In [ ]:
groundrf = cs_detection_refactor.ClearskyDetection.read_pickle('srrl_ground_1.pkl.gz')

In [ ]:
groundrf.df.index = groundrf.df.index.tz_convert('MST')

In [ ]:
groundrf.trim_dates('10-01-2015', '10-15-2015')

In [ ]:
groundrf.time_from_solar_noon('Clearsky GHI pvlib', 'tfn')

In [ ]:
test = groundrf

In [ ]:
%%time
import warnings
warnings.simplefilter("ignore")
pred = test.iter_predict_daily(feature_cols, 'GHI', 'Clearsky GHI pvlib', clf, 11)
pred = pred.astype(bool)
# %load_ext line_profiler
# %lprun -f test.calc_all_window_metrics test.iter_predict_daily(feature_cols, 'GHI', 'Clearsky GHI pvlib', clf, 11, smooth=False, tol=1.0e-6, n_iter=2)

In [ ]:
pred.to_csv('tmp_new.csv')

In [ ]:
vis = visualize.Visualizer()

In [ ]:
vis.add_line_ser(test.df['GHI'], 'GHI')
vis.add_line_ser(test.df['Clearsky GHI pvlib'], 'GHI_cs')
vis.add_circle_ser(test.df[(test.df['sky_status pvlib'] == 0) & (pred)]['GHI'], 'ML clear only')
vis.add_circle_ser(test.df[(test.df['sky_status pvlib'] == 1) & (~pred)]['GHI'], 'PVLib clear only')
vis.add_circle_ser(test.df[(test.df['sky_status pvlib'] == 1) & (pred)]['GHI'], 'ML+PVLib clear only')

In [ ]:
vis.show()

In [ ]:
cm = metrics.confusion_matrix(test.df['sky_status pvlib'].values, pred)
vis = visualize.Visualizer()
vis.plot_confusion_matrix(cm, labels=['cloudy', 'clear'])

In [ ]:
for f, i in zip(feature_cols, clf.feature_importances_):
    print(f, i)